# verify parquet

This notebook is for checking the output of the parquet process from the images_to_parquet script.

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
root = "gs://dsgt-clef-snakeclef-2024"
! date
! gcloud storage ls {root}/data/parquet_files

Wed Feb  7 22:01:06 UTC 2024


gs://dsgt-clef-snakeclef-2024/data/parquet_files/
gs://dsgt-clef-snakeclef-2024/data/parquet_files/SnakeCLEF2023-train-large_size/
gs://dsgt-clef-snakeclef-2024/data/parquet_files/SnakeCLEF2023-train-medium_size/
gs://dsgt-clef-snakeclef-2024/data/parquet_files/SnakeCLEF2023-train-small_size/
gs://dsgt-clef-snakeclef-2024/data/parquet_files/acm_image_data_test_repartition/


In [3]:
! gcloud storage ls {root}/data/parquet_files/SnakeCLEF2023-train-medium_size/ | wc -l
! gcloud storage du --readable-sizes --summarize {root}/data/parquet_files/SnakeCLEF2023-train-medium_size/

205
6.87GiB      gs://dsgt-clef-snakeclef-2024/data/parquet_files/SnakeCLEF2023-train-medium_size/


In [4]:
from snakeclef.utils import get_spark
from pyspark.sql.types import (
    StructType,
    StructField,
    StringType,
    BinaryType,
    IntegerType,
    BooleanType,
)

# Define the schema based on the provided structure
schema = StructType(
    [
        StructField("image_path", StringType(), True),
        StructField("path", StringType(), True),
        StructField("folder_name", StringType(), False),
        StructField("year", StringType(), True),
        StructField("binomial_name", StringType(), True),
        StructField("file_name", StringType(), True),
        StructField("data", BinaryType(), True),
        StructField("observation_id", IntegerType(), True),
        StructField("endemic", BooleanType(), True),
        StructField("code", StringType(), True),
        StructField("class_id", IntegerType(), True),
        StructField("subset", StringType(), True),
    ]
)

# https://knowledge.informatica.com/s/article/000196886?language=en_US
# The vectorized reader will run out of memory (8gb) with the default batch size, so
# this is one way of handling the issue. This is likely due to the fact that the data
# column is so damn big, and treated as binary data instead of something like a string.
# We might also be able to avoid this if we don't cache the fields into memory, but this
# this needs to be validated by hand.
spark = get_spark(
    **{
        # "spark.sql.parquet.columnarReaderBatchSize": 512,
        "spark.sql.parquet.enableVectorizedReader": False,
    }
)

# Load dataframe
gcs_path = (
    "gs://dsgt-clef-snakeclef-2024/data/parquet_files/SnakeCLEF2023-train-medium_size"
)
df = spark.read.schema(schema).parquet(gcs_path)
df.printSchema()
df.show(1, vertical=True, truncate=False)
df.count()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/02/07 22:01:37 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
24/02/07 22:01:37 WARN SparkConf: Note that spark.local.dir will be overridden by the value set by the cluster manager (via SPARK_LOCAL_DIRS in mesos/standalone/kubernetes and LOCAL_DIRS in YARN).


root
 |-- image_path: string (nullable = true)
 |-- path: string (nullable = true)
 |-- folder_name: string (nullable = true)
 |-- year: string (nullable = true)
 |-- binomial_name: string (nullable = true)
 |-- file_name: string (nullable = true)
 |-- data: binary (nullable = true)
 |-- observation_id: integer (nullable = true)
 |-- endemic: boolean (nullable = true)
 |-- code: string (nullable = true)
 |-- class_id: integer (nullable = true)
 |-- subset: string (nullable = true)



-RECORD 0-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

68771

In [5]:
# let's do this again and see how long it takes to cache the files
df = df.drop("data").cache()
%time df.count()

CPU times: user 34 ms, sys: 14.9 ms, total: 49 ms
Wall time: 14.4 s


68771

In [6]:
(df.groupBy("binomial_name", "code").count().orderBy("count", ascending=False).show())

+--------------------+----+-----+
|       binomial_name|code|count|
+--------------------+----+-----+
|Bothriechis_schle...|  EC|  131|
|Cubophis_cantheri...|  CU|  129|
| Spilotes_sulphureus|  EC|  127|
| Gloydius_brevicauda|  KR|  113|
|   Cacophis_krefftii|  AU|  109|
|      Elaphe_anomala|  KR|  104|
|Oocatochus_rufodo...|  KR|   94|
|Gloydius_intermedius|  KR|   94|
| Pseudonaja_mengdeni|  AU|   92|
|        Elaphe_dione|  KR|   91|
|       Furina_ornata|  AU|   87|
|Gloydius_ussuriensis|  KR|   82|
|Bothrocophias_mic...|  EC|   81|
|Pseudagkistrodon_...|  TW|   80|
| Gloydius_blomhoffii|  JP|   79|
|Leptodeira_splendida|  MX|   79|
|    Tantilla_relicta|  US|   78|
| Rhabdophis_tigrinus|  KR|   75|
| Crotalus_mitchellii|  MX|   74|
|      Furina_diadema|  AU|   73|
+--------------------+----+-----+
only showing top 20 rows



In [7]:
df.select("binomial_name").distinct().count(), df.select("code").distinct().count()

(1749, 207)

In [8]:
df.groupBy("binomial_name").count().orderBy("count", ascending=False).show()

+--------------------+-----+
|       binomial_name|count|
+--------------------+-----+
|       Natrix_natrix|  732|
| Coronella_austriaca|  670|
|   Natrix_tessellata|  665|
|        Vipera_berus|  570|
|Indotyphlops_bram...|  484|
| Zamenis_longissimus|  404|
|Psammodynastes_pu...|  337|
|   Imantodes_cenchoa|  332|
|       Boa_imperator|  316|
|   Spilotes_pullatus|  299|
|    Natrix_helvetica|  295|
| Leptophis_ahaetulla|  264|
|        Ptyas_mucosa|  259|
|Bothriechis_schle...|  251|
|Trimeresurus_albo...|  237|
|      Bothrops_atrox|  232|
|    Vipera_ammodytes|  229|
|     Boa_constrictor|  227|
|      Bitis_arietans|  224|
|   Ahaetulla_prasina|  219|
+--------------------+-----+
only showing top 20 rows

